In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install transformers datasets peft accelerate bitsandbytes trl safetensors torch --no-cache

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.1/199.1 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.3/297.3 kB 10.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.2/102.2 MB 75.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.0/225.0 kB 208.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 206.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 185.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 185.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.1/80.1 kB 159.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 116.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 229.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 168.2 MB/s eta 0:00:00
    

In [46]:
import torch
import pandas as pd
from functools import partial
from datasets import Dataset
from transformers import TrainingArguments
import time
import transformers
from sklearn.model_selection import train_test_split
from peft import LoraConfig, prepare_model_for_kbit_training, get_peft_model
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

column_names = ['H', 'RH', 'E']
# base_path = '/content/drive/My Drive/Colab Notebooks/CSCI 564 NLP'
# df = pd.read_csv(f'{base_path}/hindi_data/romanized_hindi_english_paper.csv', names=column_names,nrows=8000)

path = '/content/drive/MyDrive/Project_544/data/hindi_data/new_romanized_hindi_english_paper_19k.csv'

df = pd.read_csv(path, names=column_names, nrows=5000)

In [48]:
# Hugging Face model name
#model_name = "microsoft/phi-2" # not the larger version - need to look into this
model_name = "TinyLlama/TinyLlama-1.1B-Chat-v1.0"
use_flash_attention = False


# BitsAndBytesConfig int-4 config
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

# Load model
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    # quantization_config=bnb_config,
    use_cache=False,
    use_flash_attention_2=use_flash_attention,
    device_map="auto",
    torch_dtype=torch.float16
)

model.config.pretraining_tp = 1

# Load tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

In [49]:
# LoRA config based on QLoRA paper
peft_config = LoraConfig(
    lora_alpha=32,
    lora_dropout=0.1,
    r=16,
    bias="none",
    task_type="CAUSAL_LM",
)
# Prepare model for training
model = prepare_model_for_kbit_training(model)
model = get_peft_model(model, peft_config)

In [50]:
# for RH to E
train_df, val_df = train_test_split(df, test_size=0.2, random_state=42)
val_df, test_df = train_test_split(val_df, test_size=0.5, random_state=42)

In [51]:
# for H to E
train_df2, val_df2 = train_df.copy(), val_df.copy()
val_df2, test_df2 = val_df.copy(), test_df.copy()

In [52]:
# for RH+H to E
train_df3, val_df3 = train_df.copy(), val_df.copy()
val_df3, test_df3 = val_df.copy(), test_df.copy()

In [53]:
results = {'Languages': [],
           'Avg Sentence BLEU' : []}
           #'Corpus BLEU' : []}

# **Hindi to English**

In [54]:
train_df, val_df = train_df, val_df
val_df, test_df = val_df, test_df

In [55]:
def create_json_record(row, prefix):
    return {
        "input_ids": f"{prefix}_{row.name}",
        "text": f"Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi: {row['H']} \nEnglish: {row['E']}"
    }
def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)
# Convert train_df and val_df into JSON format
# train_dataset = [create_json_record(row, "train") for _, row in train_df.iterrows()]
# val_dataset = [create_json_record(row, "val") for _, row in val_df.iterrows()]


def create_prompt(row):
    return f"Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: {row['H']} \nEnglish: {row['E']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H', 'RH','E']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


In [56]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: नव्योत्तर काल की कई धाराएं हैं - एक पश्चिम की नकल को छोड एक अपनी वाणी पाना \nEnglish: There are several stream of modern era- one to leave the copy of western language ti find one won voice, second away from difficult language to simple language; three on the question of life and society unconfused discussion.', "Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: खेल ने 18 वीं शताब्दी में प्रमुख विकास किया और यह इंग्लैंड का राष्ट्रीय खेल बन गया. शर्त नें उस विकास में महत्वपूर्ण भूमिका निभाई साथ ही अमीर समर्थकों ने अपनी XI खिलाड़ियों की टीम तैयार की. लंदन में १७०७ में क्रिकेट बहुत प्रसिद्ध था और फिन्सबरी में आर्टिलरी ग्राउंड (Artillery Ground) के मैच में बहुत बड़ी भीड़ इकठ्ठी होती थी. खेल के सिंगल विकेट (single wicket) रूप ने बहुत बड़ी संख्या में भरी भीड़ को आकर्षित किया.गेंदबाजी १७६० के आस

In [57]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: बस वही नहीं, \nEnglish: Not only that,', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: बल्लेबाजों की भूमिका रन बनने के साथ और ओवर पूरे होने के साथ बदलती रहती है। \nEnglish: Batsman changes its side while making runs or the over is completed.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: अगर तुममें थोड़ा और सब्र होता तो तुम कामयाब हो जाते। \nEnglish: With a little more patience, you would have succeeded.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi: जंग हमारे हित में जा रहा है। \nEnglish: The war is going in our favor.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\n

In [58]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [59]:
print(type(train_dataset['text'][0]))

<class 'str'>


In [60]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=1.1827201843261719, metrics={'train_runtime': 195.5185, 'train_samples_per_second': 1.023, 'train_steps_per_second': 0.256, 'total_flos': 130831472099328.0, 'train_loss': 1.1827201843261719, 'epoch': 0.05})

In [61]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

sources = test_df['H'].to_list()
references = test_df['E'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(sources)):

    inputs = tokenizer(f'''Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi: {sources[i]} \nEnglish:''', return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nEnglish: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t.split())
    # translations.append(reference.split())
    r.append(references[i].split())  # Note: reference must be a list of lists for corpus_bleu

In [62]:
print(s)
print(r)

[['The', 'reason', 'for', 'this', 'is', 'that', 'the', 'remi', 'is', 'so', 'old.'], ['He', 'was', 'a', 'very', 'powerful', 'ruler.'], ['If', "it's", 'too', 'much,', 'then', 'a', 'little', 'bit', 'of', 'water.'], ['I', 'am', 'tired', 'of', 'work.'], ['To', 'find', 'Hindi', 'words,', 'you', 'need', 'to', 'download', 'Hindi-English', 'dictionary.'], ['We', 'have', 'worked', 'in', 'India.'], ['There', 'is', 'no', 'such', 'thing', 'as', 'a', 'house', 'in', 'her.'], ['Yes,', 'I', 'am', 'very', 'happy.'], ['We', 'will', 'go', 'first', 'and', 'then', 'we', 'will', 'come', 'back.'], ['The', 'best-selling', 'book', 'of', 'India', '(ISBN', '81-88086-'], ['There', 'are', 'a', 'lot', 'of', 'students', 'in', 'this', 'school.'], ['This', 'color', 'is', 'what?'], ['Thank', 'you', 'for', 'your', 'kindness.'], ['I', "don't", 'speak', 'English.'], ['We', 'are', 'living', 'in', 'the', 'city.'], ['Is', 'it', 'true?'], ['The', 'city', 'of', 'Ravi', 'Das', 'Nagar'], ['The', 'last', 'of', 'the', 'three', 'was

In [63]:
scores = []

avg = 0

for i in s:
  # score = sentence_bleu(r, i, weights=[0.001,0.001,0,0])
  # score = sentence_bleu(r, i, weights=[0.25,0.005,0,0]) # unigram, bigram, trigram, quadrigram
  score = sentence_bleu(r, i, weights=[0.33,0.33,0.33,0])  # unigram, bigram, trigram, quadrigram - weights=[0.25,0.15,0,0]
  scores.append(score)
  avg += score

avg = avg/len(s)
#print(scores)
print("Average BLEU score: ", avg)

/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Average BLEU score:  0.18557990626508364


In [ ]:
cb = corpus_bleu(r, s, weights=[1,0,0,0]) #0.0001m
print(cb)

In [65]:
results['Languages'].append('Hindi -> English')
results['Avg Sentence BLEU'].append(avg)
# results['Corpus BLEU'].append(cb)

In [ ]:
# peft_trainer.save_model('/content/drive/My Drive/CSCI544ProjOutput/saved_model')
# tokenizer.save_pretrained('/content/drive/My Drive/CSCI544ProjOutput/saved_tokenizer')

#**Romanized Hindi to English**

In [66]:
train_df, val_df = train_df2, val_df2
val_df, test_df = val_df2, test_df2

In [67]:
def create_json_record(row, prefix):
    return {
        "input_ids": f"{prefix}_{row.name}",
        "text": f"Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: {row['RH']} \nEnglish: {row['E']}"
    }
def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)
# Convert train_df and val_df into JSON format
# train_dataset = [create_json_record(row, "train") for _, row in train_df.iterrows()]
# val_dataset = [create_json_record(row, "val") for _, row in val_df.iterrows()]


def create_prompt(row):
    return f"Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: {row['RH']} ]\nEnglish: {row['E']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H', 'RH','E']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


In [68]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: navyottar call key kaee dhaaraaen hain - ack paschim key nakal quo chhod ack apni vaani panna ]\nEnglish: There are several stream of modern era- one to leave the copy of western language ti find one won voice, second away from difficult language to simple language; three on the question of life and society unconfused discussion.', "Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: khel nay 18 ween shatabdi main pramukh vikas kiya our yeah england kaa rashtriya khel bunn gaya. shart nein usa vikas main mahatvapurna bhoomika nibhai saath hee ameer samarthakon nay apni xi khilaadiyon key team taiyar key. landan main 1707 main cricket bahut prasiddh tha our finsbury main artillery ground (artillery ground) key match main bahut badee bheed ikatthi hoti thee. khel

In [69]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: bus vahee nahin, ]\nEnglish: Not only that,', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: ballebaajon key bhoomika rann banane key saath our over poore honey key saath badalati rahati hai. ]\nEnglish: Batsman changes its side while making runs or the over is completed.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: agar tumamen thoda our sabr hota too tum kamyab how jaate. ]\nEnglish: With a little more patience, you would have succeeded.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language.\nHindi Transliterated: jung hamare hita main jaa rahaa hai. ]\nEnglish: The war is going in our favor.', 'Transla

In [70]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [ ]:
print(type(train_dataset['text'][0]))

In [71]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=1.968774642944336, metrics={'train_runtime': 130.0259, 'train_samples_per_second': 1.538, 'train_steps_per_second': 0.385, 'total_flos': 93930925670400.0, 'train_loss': 1.968774642944336, 'epoch': 0.05})

In [ ]:
# model = AutoModelForCausalLM.from_pretrained('/content/drive/My Drive/peft-dialogue-summary-training-1712294967/checkpoint-375')
# tokenizer = AutoTokenizer.from_pretrained('/content/drive/My Drive/CSCI544ProjOutput/peft-dialogue-summary-training-1712294967/checkpoint-375',trust_remote_code=True)

In [72]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

sources = test_df['RH'].to_list()
references = test_df['E'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(sources)):

    inputs = tokenizer(f'''Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: {sources[i]} \nEnglish:''', return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nEnglish: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t.split())
    # translations.append(reference.split())
    r.append(references[i].split())  # Note: reference must be a list of lists for corpus_bleu

In [73]:
print(s)
print(r)

[["It's", 'a', 'big', 'car.'], ['He', 'was', 'a', 'very', 'tall', 'man.'], ['If', 'you', 'have', 'coffee,', 'you', 'should', 'drink', 'water', 'too.'], ['I', 'have', 'a', 'rose', 'in', 'my', 'garden.'], ['I', "don't", 'know', 'how', 'to', 'use', 'Firefox.'], ['I', 'worked', 'for', 'my', 'country.'], ['There', 'is', 'no', 'job', 'for', 'me.'], ["I'm", 'not', 'very', 'good', 'at', 'it.'], ['I', 'was', 'just', 'about', 'to', 'leave.'], ['The', 'book', 'is', 'a', 'must-have', 'for', 'every', 'woman', 'who', 'wants', 'to', 'know', 'more', 'about', 'the', 'Indian', 'Constitution.'], ['There', 'are', 'many', 'students', 'in', 'this', 'school.', ']'], ['Do', 'you', 'know', 'what', 'time', 'it', 'is?'], ["It's", 'a', 'good', 'idea.'], ['I', "don't", 'know', 'how', 'to', 'cook.', ']'], ['We', 'live', 'in', 'a', 'house.'], ['what', 'is', 'the', 'main', 'thing?'], ['the', 'village', 'is', 'in', 'the', 'city'], ['The', 'Indian', 'National', 'Congress', 'was', 'the', 'main', 'opposition', 'party', '

In [74]:
scores = []

avg = 0

for i in s:
  # score = sentence_bleu(r, i, weights=[0.001,0.001,0,0])
  score = sentence_bleu(r, i, weights=[0.33,0.33,0.33,0]) # unigram, bigram, trigram, quadrigram
  scores.append(score)
  avg += score

avg = avg/len(s)
# print(scores)
print("Average BLEU score: ", avg)

/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Average BLEU score:  0.224853130747326


In [ ]:
score = corpus_bleu(r, s, weights=[0.25,0.0001,0,0])
print("Corpus BLEU score: ", score)

In [75]:
results

{'Languages': ['Hindi -> English'], 'Avg Sentence BLEU': [0.18557990626508364]}

In [76]:
results['Languages'].append('Romanized Hindi -> English')
results['Avg Sentence BLEU'].append(avg)
# results['Corpus BLEU'].append(score)

In [ ]:
# peft_trainer.save_model('/content/drive/My Drive/CSCI544ProjOutput/saved_model')
# tokenizer.save_pretrained('/content/drive/My Drive/CSCI544ProjOutput/saved_tokenizer')

# **RH + H to English**

In [77]:
train_df, val_df = train_df3, val_df3
val_df, test_df = val_df3, test_df3

In [78]:
def create_json_record(row, prefix):
    return {
        "input_ids": f"{prefix}_{row.name}",
        "text": f"Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: {row['H']} {row['RH']} \nEnglish: {row['E']}"
    }
def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)
# Convert train_df and val_df into JSON format
# train_dataset = [create_json_record(row, "train") for _, row in train_df.iterrows()]
# val_dataset = [create_json_record(row, "val") for _, row in val_df.iterrows()]


def create_prompt(row):
    return f"Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: {row['H']} {row['RH']} \nEnglish: {row['E']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H', 'RH','E']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


In [79]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: नव्योत्तर काल की कई धाराएं हैं - एक पश्चिम की नकल को छोड एक अपनी वाणी पाना navyottar call key kaee dhaaraaen hain - ack paschim key nakal quo chhod ack apni vaani panna \nEnglish: There are several stream of modern era- one to leave the copy of western language ti find one won voice, second away from difficult language to simple language; three on the question of life and society unconfused discussion.', "Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: खेल ने 18 वीं शताब्दी में प्रमुख विकास किया और यह इंग्लैंड का राष्ट्रीय खेल बन गया. शर्त नें उस विकास में महत्वपूर्ण भूमिका निभाई साथ ही अमीर समर्थकों ने अपनी XI खिलाड़ियों की टीम तैयार की. लंदन में १७०७ में क्रिकेट बहुत प्रसिद्ध था और फिन्सबरी में आर्टिलरी ग्राउंड (Artillery Ground) के मैच में बहुत बड़ी भी

In [80]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

{'text': ['Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: बस वही नहीं, bus vahee nahin, \nEnglish: Not only that,', 'Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: बल्लेबाजों की भूमिका रन बनने के साथ और ओवर पूरे होने के साथ बदलती रहती है। ballebaajon key bhoomika rann banane key saath our over poore honey key saath badalati rahati hai. \nEnglish: Batsman changes its side while making runs or the over is completed.', 'Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi Transliterated: अगर तुममें थोड़ा और सब्र होता तो तुम कामयाब हो जाते। agar tumamen thoda our sabr hota too tum kamyab how jaate. \nEnglish: With a little more patience, you would have succeeded.', 'Translate the following sentences from Hindi to English. The output should be in Eng

In [81]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [82]:
print(type(train_dataset['text'][0]))

<class 'str'>


In [83]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=1.1251400756835936, metrics={'train_runtime': 248.7196, 'train_samples_per_second': 0.804, 'train_steps_per_second': 0.201, 'total_flos': 166624753311744.0, 'train_loss': 1.1251400756835936, 'epoch': 0.05})

In [ ]:
# model = AutoModelForCausalLM.from_pretrained('/content/drive/My Drive/peft-dialogue-summary-training-1712294967/checkpoint-375')
# tokenizer = AutoTokenizer.from_pretrained('/content/drive/My Drive/CSCI544ProjOutput/peft-dialogue-summary-training-1712294967/checkpoint-375',trust_remote_code=True)

In [84]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

rh = test_df['RH'].to_list()
h = test_df['H'].to_list()
references = test_df['E'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(rh)):

    inputs = tokenizer(f'''Translate the following sentences from Hindi to English. The output should be in English and no other language. \nHindi: {h[i]} {rh[i]} \nEnglish:''', return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nEnglish: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t.split())
    # translations.append(reference.split())
    r.append(references[i].split())  # Note: reference must be a list of lists for corpus_bleu

In [85]:
scores = []

avg = 0

for i in s:
  # score = sentence_bleu(r, i, weights=[0.001,0.001,0,0])
  score = sentence_bleu(r, i, weights=[0.33,0.33,0.33,0]) # unigram, bigram, trigram, quadrigram
  scores.append(score)
  avg += score

avg = avg/len(s)
# print(scores)
print("Average BLEU score: ", avg)

/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Average BLEU score:  0.18099862907111494


In [ ]:
cb = corpus_bleu(r, s, weights=[0.25,0.0001,0,0])
print(cb)

In [86]:
results

{'Languages': ['Hindi -> English', 'Romanized Hindi -> English'],
 'Avg Sentence BLEU': [0.18557990626508364, 0.224853130747326]}

In [87]:
results['Languages'].append('Hindi + Romanized Hindi -> English')
results['Avg Sentence BLEU'].append(avg)
# results['Corpus BLEU'].append(cb)

# **Results**

In [88]:
results_df = pd.DataFrame(results)
results_df

Languages  Avg Sentence BLEU
0                    Hindi -> English           0.185580
1          Romanized Hindi -> English           0.224853
2  Hindi + Romanized Hindi -> English           0.180999